In [29]:
import requests
import lxml.html as lh
import bs4 as bs
import urllib.request
import numpy as np 
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
!conda install -c conda-forge folium=0.5.0 --yes
import folium

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    folium-0.5.0               |             py_0          45 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    branca-0.3.1               |             py_0          25 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    altair-4.0.1               |             py_0         575 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.0 MB

The following NEW packages will be 

In [30]:
import matplotlib.cm as cm
import matplotlib.colors as colors

In [69]:
import requests
from pandas.io.json import json_normalize 

# Defining the dataset for the neighbourhoods

In [2]:
url ='https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
res = requests.get(url)
soup = bs.BeautifulSoup(res.content,'lxml')
table = soup.find_all('table')[0]
df = pd.read_html(str(table))
data = pd.read_json(df[0].to_json(orient='records'))

In [3]:
data.head()

Borough     Neighbourhood Postcode
0      Not assigned      Not assigned      M1A
1      Not assigned      Not assigned      M2A
2        North York         Parkwoods      M3A
3        North York  Victoria Village      M4A
4  Downtown Toronto      Harbourfront      M5A

In [4]:
data = data[data['Borough'] != 'Not assigned']

In [5]:
data = data.groupby(['Borough', 'Postcode'], as_index=False).agg(','.join)

In [6]:
data.head()

Borough Postcode               Neighbourhood
0  Central Toronto      M4N               Lawrence Park
1  Central Toronto      M4P            Davisville North
2  Central Toronto      M4R          North Toronto West
3  Central Toronto      M4S                  Davisville
4  Central Toronto      M4T  Moore Park,Summerhill East

In [7]:
data['Neighbourhood'] = np.where(data['Neighbourhood'] == 'Not assigned', data['Borough'], data['Neighbourhood'])

In [8]:
data.shape

(103, 3)

In [9]:
geospatial_url = "https://cocl.us/Geospatial_data"
geodata = pd.read_csv(geospatial_url)

In [10]:
geodata.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [11]:
geodata.columns = ['Postcode', 'Latitude', 'Longitude']

In [12]:
all_data = pd.merge(data, geodata, on='Postcode')

In [13]:
all_data.head()

Borough Postcode               Neighbourhood   Latitude  Longitude
0  Central Toronto      M4N               Lawrence Park  43.728020 -79.388790
1  Central Toronto      M4P            Davisville North  43.712751 -79.390197
2  Central Toronto      M4R          North Toronto West  43.715383 -79.405678
3  Central Toronto      M4S                  Davisville  43.704324 -79.388790
4  Central Toronto      M4T  Moore Park,Summerhill East  43.689574 -79.383160

In [14]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(all_data['Borough'].unique()),
        all_data.shape[0]
    )
)

The dataframe has 11 boroughs and 103 neighborhoods.


In [15]:
all_data['Coordinates'] = list(zip(all_data['Latitude'], all_data['Longitude']))

In [16]:
all_data.head()

Borough Postcode               Neighbourhood   Latitude  Longitude  \
0  Central Toronto      M4N               Lawrence Park  43.728020 -79.388790   
1  Central Toronto      M4P            Davisville North  43.712751 -79.390197   
2  Central Toronto      M4R          North Toronto West  43.715383 -79.405678   
3  Central Toronto      M4S                  Davisville  43.704324 -79.388790   
4  Central Toronto      M4T  Moore Park,Summerhill East  43.689574 -79.383160   

                        Coordinates  
0         (43.7280205, -79.3887901)  
1         (43.7127511, -79.3901975)  
2  (43.7153834, -79.40567840000001)  
3         (43.7043244, -79.3887901)  
4  (43.6895743, -79.38315990000001)

In [17]:
from geopy.geocoders import Nominatim

In [44]:
all_data

Borough Postcode  \
0     Central Toronto      M4N   
1     Central Toronto      M4P   
2     Central Toronto      M4R   
3     Central Toronto      M4S   
4     Central Toronto      M4T   
5     Central Toronto      M4V   
6     Central Toronto      M5N   
7     Central Toronto      M5P   
8     Central Toronto      M5R   
9    Downtown Toronto      M4W   
10   Downtown Toronto      M4X   
11   Downtown Toronto      M4Y   
12   Downtown Toronto      M5A   
13   Downtown Toronto      M5B   
14   Downtown Toronto      M5C   
15   Downtown Toronto      M5E   
16   Downtown Toronto      M5G   
17   Downtown Toronto      M5H   
18   Downtown Toronto      M5J   
19   Downtown Toronto      M5K   
20   Downtown Toronto      M5L   
21   Downtown Toronto      M5S   
22   Downtown Toronto      M5T   
23   Downtown Toronto      M5V   
24   Downtown Toronto      M5W   
25   Downtown Toronto      M5X   
26   Downtown Toronto      M6G   
27   Downtown Toronto      M7A   
28       East Toronto      M4E   
29       East Toronto      M4K   
..                ...      ...   
73         North York      M9M   
74       Queen's Park      M9A   
75        Scarborough      M1B   
76        Scarborough      M1C   
77        Scarborough      M1E   
78        Scarborough      M1G   
79        Scarborough      M1H   
80        Scarborough      M1J   
81        Scarborough      M1K   
82        Scarborough      M1L   
83        Scarborough      M1M   
84        Scarborough      M1N   
85        Scarborough      M1P   
86        Scarborough      M1R   
87        Scarborough      M1S   
88        Scarborough      M1T   
89        Scarborough      M1V   
90        Scarborough      M1W   
91        Scarborough      M1X   
92       West Toronto      M6H   
93       West Toronto      M6J   
94       West Toronto      M6K   
95       West Toronto      M6P   
96       West Toronto      M6R   
97       West Toronto      M6S   
98               York      M6C   
99               York      M6E   
100              York      M6M   
101              York      M6N   
102              York      M9N   

                                         Neighbourhood   Latitude  Longitude  \
0                                        Lawrence Park  43.728020 -79.388790   
1                                     Davisville North  43.712751 -79.390197   
2                                   North Toronto West  43.715383 -79.405678   
3                                           Davisville  43.704324 -79.388790   
4                           Moore Park,Summerhill East  43.689574 -79.383160   
5    Deer Park,Forest Hill SE,Rathnelly,South Hill,...  43.686412 -79.400049   
6                                             Roselawn  43.711695 -79.416936   
7                   Forest Hill North,Forest Hill West  43.696948 -79.411307   
8                    The Annex,North Midtown,Yorkville  43.672710 -79.405678   
9                                             Rosedale  43.679563 -79.377529   
10                          Cabbagetown,St. James Town  43.667967 -79.367675   
11                                Church and Wellesley  43.665860 -79.383160   
12                                        Harbourfront  43.654260 -79.360636   
13                             Ryerson,Garden District  43.657162 -79.378937   
14                                      St. James Town  43.651494 -79.375418   
15                                         Berczy Park  43.644771 -79.373306   
16                                  Central Bay Street  43.657952 -79.387383   
17                              Adelaide,King,Richmond  43.650571 -79.384568   
18     Harbourfront East,Toronto Islands,Union Station  43.640816 -79.381752   
19             Design Exchange,Toronto Dominion Centre  43.647177 -79.381576   
20                       Commerce Court,Victoria Hotel  43.648198 -79.379817   
21                       Harbord,University of Toronto  43.662696 -79.400049   
22             Chinatown,Grange Park,Kensington Market  43.653206

In [36]:
all_data.dtypes

Borough           object
Postcode          object
Neighbourhood     object
Latitude         float64
Longitude        float64
Coordinates       object
dtype: object

# Creating Toronto map and adding neighbourhoods markers on it

In [45]:
to_latitude = 43.651070
to_longitude = -79.347015
map_toronto = folium.Map(location=[to_latitude, to_longitude], zoom_start=11)
map_toronto

In [131]:
for lat, lng, label in zip(all_data['Latitude'], all_data['Longitude'], all_data['Neighbourhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

# Request for finding the venues in Foursquare

In [97]:
search_query = 'Bank'

In [98]:
CLIENT_ID = 'VLUV4U1XCOIIQ5QRWWIC1CXARC1CXT1IWBDPCZ1GV0SG2LD3'
CLIENT_SECRET = '0G4GCA3KQGJ141H4HNPGNFMQMK0SFS4OLJUYONWSL0UI0YDJ'
latitude = all_data.loc[1,'Latitude']
longitude = all_data.loc[1,'Longitude']
radius = 700
VERSION = '20180605'
LIMIT = 100

Firstly I test the dataset

In [99]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=VLUV4U1XCOIIQ5QRWWIC1CXARC1CXT1IWBDPCZ1GV0SG2LD3&client_secret=0G4GCA3KQGJ141H4HNPGNFMQMK0SFS4OLJUYONWSL0UI0YDJ&ll=43.7127511,-79.3901975&v=20180605&query=Bank&radius=700&limit=100'

In [123]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e3d905e71c428001b8f03e1'},
 'response': {'venues': [{'id': '4b310f84f964a52062ff24e3',
    'name': 'BMO Bank of Montreal',
    'location': {'address': '2444 Yonge St.',
     'crossStreet': 'at Roselawn Ave.',
     'lat': 43.710695669191686,
     'lng': -79.39943790435791,
     'labeledLatLngs': [{'label': 'display',
       'lat': 43.710695669191686,
       'lng': -79.39943790435791}],
     'distance': 777,
     'postalCode': 'M4P 2H4',
     'cc': 'CA',
     'city': 'Toronto',
     'state': 'ON',
     'country': 'Canada',
     'formattedAddress': ['2444 Yonge St. (at Roselawn Ave.)',
      'Toronto ON M4P 2H4',
      'Canada']},
    'categories': [{'id': '4bf58dd8d48988d10a951735',
      'name': 'Bank',
      'pluralName': 'Banks',
      'shortName': 'Bank',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/financial_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1581093105',
    'hasPerk': False},
  

It works, so I'll define a function to get the venues from all the neighbourhoods

In [120]:
def getNearbyVenues(names, latitudes, longitudes, radius=700):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&query={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION,
            search_query,
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [121]:
toronto_venues = getNearbyVenues(names=all_data['Neighbourhood'],
                                   latitudes=all_data['Latitude'],
                                   longitudes=all_data['Longitude']
                                  )

Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park,Summerhill East
Deer Park,Forest Hill SE,Rathnelly,South Hill,Summerhill West
Roselawn
Forest Hill North,Forest Hill West
The Annex,North Midtown,Yorkville
Rosedale
Cabbagetown,St. James Town
Church and Wellesley
Harbourfront
Ryerson,Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide,King,Richmond
Harbourfront East,Toronto Islands,Union Station
Design Exchange,Toronto Dominion Centre
Commerce Court,Victoria Hotel
Harbord,University of Toronto
Chinatown,Grange Park,Kensington Market
CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara
Stn A PO Boxes 25 The Esplanade
First Canadian Place,Underground city
Christie
Queen's Park
The Beaches
The Danforth West,Riverdale
The Beaches West,India Bazaar
Studio District
Business Reply Mail Processing Centre 969 Eastern
Woodbine Gardens,Parkview Hill
Woodbine Heights
Leaside
Thorncliffe Park
East Toronto
Humber

In [122]:
toronto_venues

Neighborhood  Neighborhood Latitude  \
0                                        Lawrence Park              43.728020   
1                                        Lawrence Park              43.728020   
2                                   North Toronto West              43.715383   
3                                   North Toronto West              43.715383   
4                                           Davisville              43.704324   
5                                           Davisville              43.704324   
6                           Moore Park,Summerhill East              43.689574   
7                           Moore Park,Summerhill East              43.689574   
8    Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
9    Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
10   Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
11   Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
12   Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
13   Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
14   Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
15   Deer Park,Forest Hill SE,Rathnelly,South Hill,...              43.686412   
16                   The Annex,North Midtown,Yorkville              43.672710   
17                                            Rosedale              43.679563   
18                          Cabbagetown,St. James Town              43.667967   
19                          Cabbagetown,St. James Town              43.667967   
20                          Cabbagetown,St. James Town              43.667967   
21                          Cabbagetown,St. James Town              43.667967   
22                                Church and Wellesley              43.665860   
23                                Church and Wellesley              43.665860   
24                                Church and Wellesley              43.665860   
25                                Church and Wellesley              43.665860   
26                                Church and Wellesley              43.665860   
27                                Church and Wellesley              43.665860   
28                                Church and Wellesley              43.665860   
29                                Church and Wellesley              43.665860   
..                                                 ...                    ...   
582                        Dovercourt Village,Dufferin              43.669005   
583                        Dovercourt Village,Dufferin              43.669005   
584                            Little Portugal,Trinity              43.647927   
585                            Little Portugal,Trinity              43.647927   
586                            Little Portugal,Trinity              43.647927   
587                            Little Portugal,Trinity              43.647927   
588                            Little Portugal,Trinity              43.647927   
589         Brockton,Exhibition Place,Parkdale Village              43.636847   
590         Brockton,Exhibition Place,Parkdale Village              43.636847   
591         Brockton,Exhibition Place,Parkdale Village              43.636847   
592         Brockton,Exhibition Place,Parkdale Village              43.636847   
593         Brockton,Exhibition Place,Parkdale Village              43.636847   
594                       High Park,The Junction South              43.661608   
595                       High Park,The Junction South              43.661608   
596                              Parkdale,Roncesvalles              43.648960   
597                              Parkdale,Roncesvalles              43.648960   
598                                  Runnymede,Swansea              43.651571   
599                                  Runnymede,Swansea              43.65

In [125]:
map_toronto_venues = folium.Map(location=[to_latitude, to_longitude], zoom_start=11)

In [132]:
for lat, lng, label in zip(toronto_venues['Venue Latitude'], toronto_venues['Venue Longitude'], toronto_venues['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto_venues)  
    
map_toronto_venues

Looks like the city center is very saturated, let's look at how many banks there are per neighbourhood

# Businesses per neighbourhood

In [134]:
per_hood = toronto_venues[['Neighborhood','Venue']]

In [144]:
per_hood.head()

Neighborhood                Venue
0       Lawrence Park  CIBC 161 Bay Street
1       Lawrence Park           Scotiabank
2  North Toronto West      TD Canada Trust
3  North Toronto West  RBC Financial Group
4          Davisville       RBC Royal Bank

In [147]:
numpy_hood = per_hood.to_numpy()
numpy_hood

array([['Lawrence Park', 'CIBC 161 Bay Street'],
       ['Lawrence Park', 'Scotiabank'],
       ['North Toronto West', 'TD Canada Trust'],
       ...,
       ['The Junction North,Runnymede', 'TD Canada Trust'],
       ['Weston', 'Money Mart'],
       ['Weston', 'Bank Of Montreal']], dtype=object)

In [149]:
def unique(numpy_hood): 
    x = np.array(numpy_hood) 
    print(np.unique(x)) 

IndexError: only integers, slices (`:`), ellipsis (`...`), numpy.newaxis (`None`) and integer or boolean arrays are valid indices